# Mesh Visualization with PyRender

This notebook loads and visualizes 3D meshes from the LOD dataset using PyRender and matplotlib for display.

In [4]:
import numpy as np
import trimesh
import pyrender
import matplotlib.pyplot as plt
import os

os.environ["PYOPENGL_PLATFORM"] = "egl"
os.environ["LIBGL_ALWAYS_SOFTWARE"] = "1"

#Config for debugging
SHOW_Y_AXIS = True

In [ ]:
lod_3_scene = trimesh.load("/home/jeans/win/aaaJAIST/resources/LOD_data_50/6/lod3.obj")
#extract the mesh from the scene
# lod_3_mesh = trimesh.util.concatenate(list(lod_3_scene.geometry.values()))
# trimesh.repair.fix_normals(lod_3_mesh)

# lod_3_scene = trimesh.Scene()
# lod_3_scene.add_geometry(lod_3_mesh)
# tranlate to origin
lod_3_scene.apply_translation(-lod_3_scene.centroid)

#show in pyrender
pyrender_scene = pyrender.Scene.from_trimesh_scene(lod_3_scene)
# add a uniform ambient term (rgb)
pyrender_scene.ambient_light = np.array([0.1, 0.1, 0.1])
#show the scene
renderer = pyrender.OffscreenRenderer(800, 600)
#add camera
camera = pyrender.PerspectiveCamera(yfov=np.pi / 2.0)
pyrender_scene.add(camera, pose=np.eye(4))

color, depth = renderer.render(pyrender_scene)


plt.figure(figsize=(10, 10))
plt.imshow(color)
plt.axis('off')
plt.show()

    

GLError: GLError(
	err = 12296,
	baseOperation = eglMakeCurrent,
	cArguments = (
		<OpenGL._opaque.EGLDisplay_pointer object at 0x751f7fb1b840>,
		<OpenGL._opaque.EGLSurface_pointer object at 0x751f81aede40>,
		<OpenGL._opaque.EGLSurface_pointer object at 0x751f81aede40>,
		<OpenGL._opaque.EGLContext_pointer object at 0x751f7fb1bac0>,
	),
	result = 0
)

In [ ]:
from trimesh.visual.material import PBRMaterial
import numpy as np

# --- load your scene & concat into a single mesh as before ---
lod_3_scene = trimesh.load("/home/jeans/win/aaaJAIST/resources/LOD_data_50/6/lod3.obj")
lod_3_mesh  = trimesh.util.concatenate(list(lod_3_scene.geometry.values()))
trimesh.repair.fix_normals(lod_3_mesh)

# --- now force opaque materials ---
# If your mesh still has a PBRMaterial on its visual:
mat = lod_3_mesh.visual.material
if isinstance(mat, PBRMaterial):
    # 1) ignore all alpha
    mat.alphaMode = "OPAQUE"
    # 2) ensure global alpha = 1
    mat.baseColorFactor[3] = 1.0

    # 3) if there's a texture with RGBA data, drop its A channel
    tex = mat.baseColorTexture
    if tex is not None:
        img = tex.image
        # only RGB, no A
        if img.shape[-1] == 4:
            tex.image = img[..., :3]

# --- build a fresh scene and show it in trimesh (or pyrender) ---
opaque_scene = trimesh.Scene()
opaque_scene.add_geometry(lod_3_mesh)
opaque_scene.show()
